Based on sergiolucero's code here: https://gist.github.com/sergiolucero/e0a6dd13494f139acd968e231906aef2
and Bert Carremans' code here: https://towardsdatascience.com/visualizing-air-pollution-with-folium-maps-4ce1a1880677

A follow up to my map of Covid-19 in Italy: https://github.com/seantibbitts/mapping-Covid-19-in-Italy/blob/master/Mapping%20Covid-19%20in%20Italy.ipynb
(View on NBViewer here: https://nbviewer.jupyter.org/github/seantibbitts/mapping-Covid-19-in-Italy/blob/master/Mapping%20Covid-19%20in%20Italy.ipynb)

In [2]:
import pandas as pd
import folium, branca
from folium.plugins import TimestampedGeoJson
from folium import Popup
from bs4 import BeautifulSoup
import requests
from datetime import datetime
from urllib.error import HTTPError

### The data is stored on Github in datestamped CSV files. Create a list of dates to pull from.

In [3]:
dates = pd.date_range(start='01-22-2020', end = datetime.now()).to_list()

In [4]:
df = pd.DataFrame()

### Download each CSV.

In [5]:
for date in dates:
    date_str = date.strftime('%m-%d-%Y')
    path = f'https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_daily_reports/{date_str}.csv'
    try:
        download_df = pd.read_csv(path)
        df = df.append(download_df)
    except HTTPError as e:
        pass

In [6]:
df0 = df.copy()

### Some of the location data is empty. Attempt to fill it by grouping by province and region and taking the max of the latitude and longitude.

In [7]:
# Start by creating a non-null primary key that can be used in the groupby
df0['province_country'] = df0['Province/State'].str.cat(df0['Country/Region'], na_rep = '')

In [8]:
# Take the max
df_max = df0.groupby('province_country')[['Latitude','Longitude']].max().reset_index()

In [9]:
# Merge the coordinates back onto the dataframe
df1 = pd.merge(df0, df_max, how = 'left', on = 'province_country')

In [10]:
# Create new latitude and longitude columns by filling NAs with the new values
df1['Latitude'] = df1['Latitude_x'].fillna(df1['Latitude_y'])
df1['Longitude'] = df1['Longitude_x'].fillna(df1['Longitude_y'])

In [11]:
# Limit dataframe to rows where the location data is not null
df2 = df1[df1['Latitude'].notnull() & df1['Longitude'].notnull()].copy()

### The 'Last Update' column is type object, not date. Transform into a datetime.

In [12]:
df2['Last Update Date'] = pd.to_datetime(df2['Last Update'], yearfirst=True)

### Set the location (chose Italy just because)

In [15]:
location = (43.0000,12.0000)

In [16]:
df3 = df2[(df2['Confirmed']>0)|(df2['Deaths']>0)|(df2['Recovered']>0)].copy()

### Define colormaps for the Confirmed, Deaths and Recovered columns

In [17]:
colormap_confirmed = branca.colormap.linear.YlOrRd_03.scale(0, df3['Confirmed'].max())
colormap_deaths = branca.colormap.LinearColormap(['#9fc8e1','#2171b5']).scale(0, df3['Deaths'].max())
colormap_recovered = branca.colormap.linear.RdYlGn_03.scale(0, df3['Recovered'].max())

### Compile feature lists for Confirmed, Deaths and Recovered columns.
#### Sort by value so that higher rates show up on top in the maps.

In [18]:
features_confirmed = []

In [19]:
for _, row in df3[df3['Confirmed']>0].sort_values('Confirmed').iterrows():
    feature = {
        'type': 'Feature',
        'geometry': {
            'type':'Point',
            'coordinates':[row['Longitude'],row['Latitude']]
        },
        'properties': {
            'time': row['Last Update Date'].date().__str__(),
            'style': {'color': colormap_confirmed(row['Confirmed'])},
            'icon': 'circle',
            'iconstyle':{
                'fillColor': colormap_confirmed(row['Confirmed']),
                'fillOpacity': 0.8,
                'stroke': 'true',
                'radius': 2
            }
        }
    }
    features_confirmed.append(feature)

In [20]:
features_deaths = []

In [21]:
for _, row in df3[df3['Deaths']>0].sort_values('Deaths').iterrows():
    feature = {
        'type': 'Feature',
        'geometry': {
            'type':'Point',
            'coordinates':[row['Longitude'],row['Latitude']]
        },
        'properties': {
            'time': row['Last Update Date'].date().__str__(),
            'style': {'color': colormap_deaths(row['Deaths'])},
            'icon': 'circle',
            'iconstyle':{
                'fillColor': colormap_deaths(row['Deaths']),
                'fillOpacity': 0.8,
                'stroke': 'true',
                'radius': 2
            }
        }
    }
    features_deaths.append(feature)

In [22]:
features_recovered = []

In [23]:
for _, row in df3[df3['Recovered']>0].sort_values('Recovered').iterrows():
    feature = {
        'type': 'Feature',
        'geometry': {
            'type':'Point',
            'coordinates':[row['Longitude'],row['Latitude']]
        },
        'properties': {
            'time': row['Last Update Date'].date().__str__(),
            'style': {'color': colormap_recovered(row['Recovered'])},
            'icon': 'circle',
            'iconstyle':{
                'fillColor': colormap_recovered(row['Recovered']),
                'fillOpacity': 0.8,
                'stroke': 'true',
                'radius': 2
            }
        }
    }
    features_recovered.append(feature)

### Initialize the map objects and add colorbars at the top

In [33]:
fm_confirmed = folium.Map(location = location, zoom_start=1, tile='stamentoner', width=800, height=400)\
.add_child(colormap_confirmed)

In [34]:
fm_deaths = folium.Map(location = location, zoom_start=1, tile='stamentoner', width=800, height=400)\
.add_child(colormap_deaths)

In [35]:
fm_recovered = folium.Map(location = location, zoom_start=1, tile='stamentoner', width=800, height=400)\
.add_child(colormap_recovered)

### Feed the features lists into TimestampedGeoJson objects and add to maps

In [36]:
TimestampedGeoJson(
    {'type': 'FeatureCollection',
    'features': features_confirmed}
    , period='P1D'
    , add_last_point=True
    , auto_play=False
    , loop=False
    , max_speed=1
    , loop_button=True
    , date_options='YYYY/MM/DD'
    , time_slider_drag_update=True
    , duration='P1D'
).add_to(fm_confirmed)

In [37]:
TimestampedGeoJson(
    {'type': 'FeatureCollection',
    'features': features_deaths}
    , period='P1D'
    , add_last_point=True
    , auto_play=False
    , loop=False
    , max_speed=1
    , loop_button=True
    , date_options='YYYY/MM/DD'
    , time_slider_drag_update=True
    , duration='P1D'
).add_to(fm_deaths)

In [38]:
TimestampedGeoJson(
    {'type': 'FeatureCollection',
    'features': features_recovered}
    , period='P1D'
    , add_last_point=True
    , auto_play=False
    , loop=False
    , max_speed=1
    , loop_button=True
    , date_options='YYYY/MM/DD'
    , time_slider_drag_update=True
    , duration='P1D'
).add_to(fm_recovered)

## Time Series Map of Confirmed Covid-19 Cases

In [39]:
fm_confirmed

## Time Series Map of Covid-19 Deaths

In [40]:
fm_deaths

## Time Series Map of Recovered Covid-19 Cases

In [41]:
fm_recovered